# Computing erfc

In [8]:
using ApproxFunFourier, ApproxFun, SpecialFunctions, SingularIntegralEquations, RiemannHilbert

Here we will consider the problem of computing the complementary error function $\mathrm{erfc}(z)$ for all $z \in \mathbb C$.  Our approach is just a reinterpretation of  $\newcommand{\E}{\mathrm{e}} \newcommand{\D}{\mathrm{d}} \newcommand{\I}{\mathrm{i}}$

__A. C. Weideman__, _Computation of the Complex Error Function_, SIAM Journal on Numerical Analysis, Vol. 31, pp. 1497-1518 (1994) 

The complementary error function is defined by
\begin{align*}
\mathrm{erfc}(z) = \frac{2}{\sqrt \pi} \int_z^\infty \E^{-s^2} \D s.
\end{align*}

The large $z$ asymptotics for this can be determined using integration by parts.  After this, we define
\begin{align*}
    \Phi(z) = \begin{cases} - \E^{z^2} \mathrm{erfc}(z) & \mathrm{Re}\, z > 0, \\ \E^{z^2} \left( 2 -  \mathrm{erfc}(z) \right) & \mathrm{Re}\, z < 0.
    \end{cases}
\end{align*}

And then it follows that $\Phi$ solves the following Riemann-Hilbert problem
\begin{align*}
\Phi_+(s) - \Phi_-(s) = 2 \E^{s^2}, \quad s \in \I \mathbb R, \quad \Phi(\infty) = 0.
\end{align*}
The orientation of $\I \mathbb R$ is that of increasing imaginary part.

The package `ApproxFunFourier.jl` includes functionality to perform an expansion of a function in the basis

$$
\begin{equation}
    f(x) \approx \sum_{j=-N}^N c_j \left( \frac{ L i + x}{ L i-x} \right)^j, \quad c_j = c_j(L).
\end{equation}
$$

And it makes sense to optimize over $L$ so that we minimize the number of terms required to reach machine accuracy.

In [12]:
f = x -> 2.0exp(-x^2)
n = 100_000
L = .1
for i = 1:50
    global n,L
    dom = PeriodicLine{false,Float64}(0.,L+.1)
    F = Fun(f,Laurent(dom))
    if length(F.coefficients) > n
        break
    end
    n = length(F.coefficients)
    L += .1
end
L
F.coefficients

109-element Array{Complex{Float64},1}:
      0.421612728122287 + 0.0im                   
     0.3717367339489732 + 5.930701355486263e-17im 
     0.3717367339489732 - 4.2161725377683085e-17im
     0.2517131932174492 + 6.035862999542042e-17im 
     0.2517131932174492 - 5.901553219508398e-17im 
    0.12503305237882914 + 4.370799242868492e-17im 
     0.1250330523788291 - 4.6047118906764774e-17im
   0.039922539075593816 + 1.9261596005139405e-17im
    0.03992253907559381 - 1.8376498920383113e-17im
   0.003993701165879765 - 1.5948369496240897e-18im
   0.003993701165879766 + 1.8564748658872235e-18im
  -0.002642365964826236 - 5.527396800840703e-18im 
  -0.002642365964826236 + 5.5372098214895415e-18im
                        ⋮                         
 4.2412260511024943e-16 + 2.0185476640704323e-17im
  4.276956159020753e-16 - 1.313601966021367e-17im 
 -4.074061187286102e-16 - 9.474664256168053e-19im 
 -4.045391239603912e-16 - 5.842064261027706e-18im 
  1.798788812942386e-16 - 4.790714260980242

The package `SingularIntegralEquations.jl` implements the `cauchy` transform:

In [13]:
dom = PeriodicLine{false,Float64}(0.,L)
F = Fun(f,Laurent(dom))
my_erfc(z) = real(z) > 0 ? -exp(-z^2)*cauchy(F,-1im*z) : 2  - exp(-z^2)*cauchy(F,-1im*z)

my_erfc (generic function with 1 method)

In [16]:
x = -1.0; println(abs(my_erfc(x) - erfc(x))/abs(erfc(x)))
x = -10000.0+1000im; println(abs(my_erfc(x) - erfc(x)))

1.158555391641698e-17
0.0
